In [1]:
%matplotlib inline
import matplotlib.pyplot as plt
import numpy as np
import pyarrow.parquet as pq
import pandas as pd
import warnings
from astropy.coordinates import SkyCoord
from astropy import units as u
import gc

In [2]:
# Mitigate against the fact that pandas has the most unstable UI in all of Python.
# I know this is gross. It's legacy code adapted for expediency. Don't @ me.
warnings.filterwarnings("ignore")

In [3]:
def read_pmsu(filename = '../ref/apj520168t3_mrt.txt',
              data=pd.DataFrame(),verbose=1,csvfile=None):
    with open(filename) as f:
        table = f.readlines()[55:]
    for i,line in enumerate(table):
        if line.strip()=='':
            continue
        try:
            if line[0:19].strip() in data.name.tolist():
                continue
        except AttributeError:
            pass
        entry = {
            'catalog':'PMSU',
            'catfile':filename,
            'source':line[0:19].strip(),
            'ggoid':int(line[0:19]),
            'ra':float(line[34:45]),
            'dec':float(line[46:57]),
            'nmag':float(line[90:96]),
            'fmag':float(line[103:110]),
            'spectype':'M',
            'specsubtype':float(line[30:33]),
            'distance':float(line[214:218]),
            }
        data = data.append(pd.Series(entry),ignore_index=True)
    return data

read_pmsu()

catalog                     catfile               source  \
0      PMSU  ../ref/apj520168t3_mrt.txt  6372076894527948789   
1      PMSU  ../ref/apj520168t3_mrt.txt  6375982386675452562   
2      PMSU  ../ref/apj520168t3_mrt.txt  6375982351239873134   
3      PMSU  ../ref/apj520168t3_mrt.txt  6375982355536938583   
4      PMSU  ../ref/apj520168t3_mrt.txt  6376721218758771355   
..      ...                         ...                  ...   
366    PMSU  ../ref/apj520168t3_mrt.txt  6385024737016287809   
367    PMSU  ../ref/apj520168t3_mrt.txt  6385024723057643751   
368    PMSU  ../ref/apj520168t3_mrt.txt  6384285878085226252   
369    PMSU  ../ref/apj520168t3_mrt.txt  6384813591053206447   
370    PMSU  ../ref/apj520168t3_mrt.txt  4491991121308680773   

                   ggoid          ra        dec    nmag    fmag spectype  \
0    6372076894527948789    1.299312  45.786010  18.729 -99.000        M   
1    6375982386675452562    2.113565  17.424250  19.308  21.562        M   
2    6375982351239873134    2.224591  20.839484  18.568 -99.000        M   
3    6375982355536938583    4.237282  20.065429  21.000  22.741        M   
4    6376721218758771355    4.337169  29.184620  20.638 -99.000        M   
..                   ...         ...        ...     ...     ...      ...   
366  6385024737016287809  343.863541 -52.302853  19.677  21.222        M   
367  6385024723057643751  345.836729 -49.726347  19.469  22.405        M   
368  6384285878085226252  350.030228 -60.065311  19.876 -99.000        M   
369  6384813591053206447  351.425655 -45.609778  20.290 -99.000        M   
370  4491991121308680773  354.573357 -41.518521  19.766 -99.000        M   

     specsubtype  distance  
0            1.0      11.5  
1            0.0      21.9  
2            4.5      11.3  
3            3.5      22.2  
4            2.0      23.5  
..           ...       ...  
366          0.5      24.7  
367          0.0      20.8  
368          0.5      20.4  
369          0.5      30.4  
370          2.0      18.5  

[371 rows x 11 columns]

In [4]:
def read_dr7(filename = '../ref/apj520168t2_mrt.txt',
             data=pd.DataFrame(),csvfile=None):
    with open(filename) as f:
        table = f.readlines()[63:]
    for i,line in enumerate(table):
        try:
            if line[0:19].strip() in data.name.tolist():
                print_inline('Skipping...')
                continue
        except AttributeError:
            pass
        entry = {
            'catalog':'DR7',
            'catfile':filename,
            'source':line[0:19].strip(),
            'ggoid':int(line[0:19]),
            'ra':float(line[41:52]),
            'dec':float(line[53:64]),
            'spectype':'M',
            'specsubtype':float(line[39:40]),
            'distance':float(line[239:244]),
            }
        data = data.append(pd.Series(entry),ignore_index=True)
    return data

read_dr7()

catalog                     catfile               source  \
0       DR7  ../ref/apj520168t2_mrt.txt  2411926227589795009   
1       DR7  ../ref/apj520168t2_mrt.txt  2415409480426589226   
2       DR7  ../ref/apj520168t2_mrt.txt  2415866877263743467   
3       DR7  ../ref/apj520168t2_mrt.txt  2415972430377917536   
4       DR7  ../ref/apj520168t2_mrt.txt  2417450174007744446   
..      ...                         ...                  ...   
181     DR7  ../ref/apj520168t2_mrt.txt  6381928518714917930   
182     DR7  ../ref/apj520168t2_mrt.txt  6381928527304853017   
183     DR7  ../ref/apj520168t2_mrt.txt  6382702557721006912   
184     DR7  ../ref/apj520168t2_mrt.txt  6387909852306343614   
185     DR7  ../ref/apj520168t2_mrt.txt  6387909899548885848   

                   ggoid          ra        dec spectype  specsubtype  \
0    2411926227589795009  151.718377   1.041589        M          1.0   
1    2415409480426589226  200.788355  -3.394583        M          6.0   
2    2415866877263743467  254.214745  60.926055        M          2.0   
3    2415972430377917536  261.468101  63.484960        M          2.0   
4    2417450174007744446   13.330920  -0.861671        M          3.0   
..                   ...         ...        ...      ...          ...   
181  6381928518714917930  157.904037   2.039601        M          0.0   
182  6381928527304853017  158.243474   1.366350        M          1.0   
183  6382702557721006912  150.261244   4.681371        M          7.0   
184  6387909852306343614  232.622890  23.673616        M          1.0   
185  6387909899548885848  239.033873  25.066171        M          2.0   

     distance  
0       948.7  
1       194.0  
2       513.9  
3       628.9  
4       526.1  
..        ...  
181     889.3  
182     336.6  
183     112.5  
184     821.1  
185     209.8  

[186 rows x 9 columns]

In [5]:
def read_lepinegaidos(filename1='../ref/aj403664t1_mrt.txt',
                      filename2='../ref/aj403664t2_mrt.txt',
                      data=pd.DataFrame(),csvfile=None):
    with open(filename1) as f1:
        table1 = f1.readlines()[41:]
    with open(filename2) as f2:
        table2 = f2.readlines()[30:]
    for i in range(len(table1)):
        try:
            if table1[i][0:16].strip() in data.name.tolist():
                continue
        except AttributeError:
            pass
        entry={
            'catalog':'LepineGaidos',
            'catfile':filename1,
            'source':table1[i][0:16].strip(),
            'ra':float(table1[i][55:65]),
            'dec':float(table1[i][67:77]),
            'spectype':table2[i][109:112].strip()[0].upper(),
            'specsubtype':float(table2[i][109:112].strip()[1:]),
            'distance':1./float(table2[i][94:101]),
            }
        data = data.append(pd.Series(entry),ignore_index=True)
    return data

read_lepinegaidos()

catalog                    catfile           source          ra  \
0     LepineGaidos  ../ref/aj403664t1_mrt.txt   PM I00001+6943    0.028531   
1     LepineGaidos  ../ref/aj403664t1_mrt.txt  PM I00003-0802S    0.087698   
2     LepineGaidos  ../ref/aj403664t1_mrt.txt   PM I00005-0533    0.144895   
3     LepineGaidos  ../ref/aj403664t1_mrt.txt   PM I00006+1829    0.163528   
4     LepineGaidos  ../ref/aj403664t1_mrt.txt   PM I00007+1624    0.195877   
...            ...                        ...              ...         ...   
8884  LepineGaidos  ../ref/aj403664t1_mrt.txt   PM I23590+2051  359.751740   
8885  LepineGaidos  ../ref/aj403664t1_mrt.txt   PM I23596+0232  359.923401   
8886  LepineGaidos  ../ref/aj403664t1_mrt.txt   PM I23596-7309  359.911499   
8887  LepineGaidos  ../ref/aj403664t1_mrt.txt   PM I23597-4405  359.936798   
8888  LepineGaidos  ../ref/aj403664t1_mrt.txt   PM I23598-3406  359.964081   

            dec spectype  specsubtype   distance  
0     69.717117        M          3.0  30.211480  
1     -8.037146        M          3.0  23.310023  
2     -5.551960        M          1.0  31.948882  
3     18.488850        K          7.0  32.573290  
4     16.402805        M          2.0  27.397260  
...         ...      ...          ...        ...  
8884  20.860765        M          4.0  18.518519  
8885   2.542501        M          2.0  29.325513  
8886 -73.155205        M          3.0  18.484288  
8887 -44.083374        M          3.0  18.181818  
8888 -34.111820        M          4.0  14.124294  

[8889 rows x 8 columns]

In [6]:
def read_shkolnik2010(filename = '../ref/apj374973t1_ascii.txt',
                      data=pd.DataFrame(),csvfile=None):
    with open(filename) as f:
        table = f.readlines()[5:35]
    for line in table:
        entries = line.split('\t')
        if len(line.split('\t'))==10:
            entries = line.split('\t')+[None]
        try:
            if entries[0] in data.name.tolist():
                continue
        except AttributeError:
            pass
        entry={
            'catalog':'Shkolnik2010',
            'catfile':filename,
            'source':entries[0],
            'ra':float(entries[1]),
            'dec':float(entries[2]),
            'spectype':None,
            'specsubtype':None,
            'distance':None,
            }
        data = data.append(pd.Series(entry),ignore_index=True)
    return data

read_shkolnik2010()

catalog                       catfile               source       ra  \
0   Shkolnik2010  ../ref/apj374973t1_ascii.txt  100624.73-301443.98  265.489   
1   Shkolnik2010  ../ref/apj374973t1_ascii.txt  101321.43-354236.93  270.235   
2   Shkolnik2010  ../ref/apj374973t1_ascii.txt  103054.53-401127.58  275.832   
3   Shkolnik2010  ../ref/apj374973t1_ascii.txt  103710.47-350501.52  274.116   
4   Shkolnik2010  ../ref/apj374973t1_ascii.txt  103952.76-353403.03  274.886   
5   Shkolnik2010  ../ref/apj374973t1_ascii.txt  110253.73-314510.57  277.441   
6   Shkolnik2010  ../ref/apj374973t1_ascii.txt  110602.46-310508.38  277.778   
7   Shkolnik2010  ../ref/apj374973t1_ascii.txt  111146.37-393734.78  282.820   
8   Shkolnik2010  ../ref/apj374973t1_ascii.txt  111152.67-440153.87  284.642   
9   Shkolnik2010  ../ref/apj374973t1_ascii.txt  111812.37-323559.09  281.095   
10  Shkolnik2010  ../ref/apj374973t1_ascii.txt  113053.55-462825.19  288.778   
11  Shkolnik2010  ../ref/apj374973t1_ascii.txt  113114.83-482627.98  289.463   
12  Shkolnik2010  ../ref/apj374973t1_ascii.txt  113456.51-364028.09  286.257   
13  Shkolnik2010  ../ref/apj374973t1_ascii.txt  113458.90-344311.59  285.575   
14  Shkolnik2010  ../ref/apj374973t1_ascii.txt  113908.06-453239.81  289.896   
15  Shkolnik2010  ../ref/apj374973t1_ascii.txt  114550.03-330213.32  287.404   
16  Shkolnik2010  ../ref/apj374973t1_ascii.txt  114808.96-375809.45  289.406   
17  Shkolnik2010  ../ref/apj374973t1_ascii.txt  120027.51-340537.17  291.035   
18  Shkolnik2010  ../ref/apj374973t1_ascii.txt  120308.07-382655.54  292.643   
19  Shkolnik2010  ../ref/apj374973t1_ascii.txt  120710.89-323053.72  292.208   
20  Shkolnik2010  ../ref/apj374973t1_ascii.txt  121907.68-410157.81  296.393   
21  Shkolnik2010  ../ref/apj374973t1_ascii.txt  121929.82-341424.54  295.447   
22  Shkolnik2010  ../ref/apj374973t1_ascii.txt  122025.78-430406.97  296.934   
23  Shkolnik2010  ../ref/apj374973t1_ascii.txt  122133.27-414029.12  296.968   
24  Shkolnik2010  ../ref/apj374973t1_ascii.txt  122408.36-313427.48  296.156   
25  Shkolnik2010  ../ref/apj374973t1_ascii.txt  122643.75-414737.31  298.004   
26  Shkolnik2010  ../ref/apj374973t1_ascii.txt  122651.35-331612.47  297.040   
27  Shkolnik2010  ../ref/apj374973t1_ascii.txt  123343.57-325126.29  298.636   
28  Shkolnik2010  ../ref/apj374973t1_ascii.txt  124543.60-370436.24  301.673   
29  Shkolnik2010  ../ref/apj374973t1_ascii.txt  125649.64-300737.37  304.317   

       dec spectype specsubtype distance  
0   20.388     None        None     None  
1   16.942     None        None     None  
2   15.176     None        None     None  
3   20.167     None        None     None  
4   20.040     None        None     None  
5   25.691     None        None     None  
6   26.590     None        None     None  
7   19.321     None        None     None  
8   15.294     None        None     None  
9   26.304     None        None     None  
10  14.173     None        None     None  
11  12.329     None        None     None  
12  23.716     None        None     None  
13  25.563     None        None     None  
14  15.501     None        None     None  
15  27.849     None        None     None  
16  23.236     None        None     None  
17  27.598     None        None     None  
18  23.465     None        None     None  
19  29.457     None        None     None  
20  21.441     None        None     None  
21  28.178     None        None     None  
22  19.442     None        None     None  
23  20.865     None        None     None  
24  30.940     None        None     None  
25  20.856     None        None     None  
26  29.320     None        None     None  
27  29.877     None        None     None  
28  25.790     None        None     None  
29  32.730     None        None     None

In [7]:
def read_shkolnik2014(filename = '../ref/aj499985t1_ascii.txt',
                      data=pd.DataFrame(),csvfile=None):
    with open(filename) as f:
        table = f.readlines()[6:233]
    for line in table:
        if line.strip()=='':
            continue
        entries = line.split('\t')
        if len(entries)==1:
            continue
        if len(line.split('\t'))==10:
            entries = line.split('\t')+[None]
        try:
            if entries[0] in data.name.tolist():
                continue
        except AttributeError:
            pass
        entry={
            'catalog':'Shkolnik2014',
            'catfile':filename,
            'source':entries[0],
            'ra':float(entries[1]),
            'dec':float(entries[2]),
            'spectype':entries[3][0],
            'specsubtype':np.array(entries[3][1:].split('-{s}'.format(
                                s=entries[3][0])),dtype='float16').mean(),
            'distance':float(entries[5]),
        }
        data = data.append(pd.Series(entry),ignore_index=True)
    return data

read_shkolnik2014()

catalog                      catfile       source          ra  \
0    Shkolnik2014  ../ref/aj499985t1_ascii.txt      TWA 2 A  167.307540   
1    Shkolnik2014  ../ref/aj499985t1_ascii.txt      TWA 2 B  167.307540   
2    Shkolnik2014  ../ref/aj499985t1_ascii.txt    TWA 3 Aab  167.616200   
3    Shkolnik2014  ../ref/aj499985t1_ascii.txt      TWA 3 B  167.616200   
4    Shkolnik2014  ../ref/aj499985t1_ascii.txt       TWA 12  170.272917   
..            ...                          ...          ...         ...   
210  Shkolnik2014  ../ref/aj499985t1_ascii.txt      GJ 4248  330.622304   
211  Shkolnik2014  ../ref/aj499985t1_ascii.txt  Gl 867 AabC  339.689894   
212  Shkolnik2014  ../ref/aj499985t1_ascii.txt       Gl 877  343.939623   
213  Shkolnik2014  ../ref/aj499985t1_ascii.txt       Gl 880  344.145020   
214  Shkolnik2014  ../ref/aj499985t1_ascii.txt       Gl 908  357.302200   

           dec spectype  specsubtype  distance  
0   -30.027720        M          2.0      46.6  
1   -30.027720        M          2.0      46.6  
2   -37.531100        M          3.0     -34.0  
3   -37.531100        M          3.5     -34.0  
4   -38.754722        M          2.0      64.1  
..         ...      ...          ...       ...  
210 -37.080894        M          3.5       7.5  
211 -20.621134        M          1.5       8.7  
212 -75.458669        M          2.5       8.6  
213  16.553432        M          1.5       6.8  
214   2.401224        M          1.0       6.0  

[215 rows x 8 columns]

In [8]:
def read_miles2017(filename = '../ref/1705.03583.txt',
                   data=pd.DataFrame(),csvfile=None):
    with open(filename) as f:
        table = f.readlines()[55:426]
    for line in table:
        entries = line.split('&')
        try:
            if entries[0].strip() in data.name.tolist():
                print_inline('Skipping {n}...'.format(n=entries[0]))
                continue # Note: This (new) catalog should actually take priority!
        except AttributeError:
            pass
        entry={
            'catalog':'MilesShkolnik2017',
            'catfile':filename,
            'source':entries[0].strip(),
            'ra':float(entries[1]),
            'dec':float(entries[2]),
            'spectype':entries[3].strip()[0],
            'distance':float(entries[6]),
        }
        if entries[3].strip()[1:]==':':
            entry['specsubtype']=None
        else:
            entry['specsubtype']=float(entries[3].strip()[1:])
        data = data.append(pd.Series(entry),ignore_index=True)
    return data

read_miles2017()

catalog                catfile            source         ra  \
0    MilesShkolnik2017  ../ref/1705.03583.txt           LHS1014    1.29780   
1    MilesShkolnik2017  ../ref/1705.03583.txt           NLTT400    2.30600   
2    MilesShkolnik2017  ../ref/1705.03583.txt           NLTT557    2.97127   
3    MilesShkolnik2017  ../ref/1705.03583.txt  00144767-6003477    3.69901   
4    MilesShkolnik2017  ../ref/1705.03583.txt            GJ1005    3.86861   
..                 ...                    ...               ...        ...   
366  MilesShkolnik2017  ../ref/1705.03583.txt           LHS3859  342.65909   
367  MilesShkolnik2017  ../ref/1705.03583.txt          LP344-47  342.68995   
368  MilesShkolnik2017  ../ref/1705.03583.txt            GT Peg  342.97426   
369  MilesShkolnik2017  ../ref/1705.03583.txt          LP401-10  343.54708   
370  MilesShkolnik2017  ../ref/1705.03583.txt             Gl877  343.93166   

          dec spectype  distance specsubtype  
0    45.78628        M      11.5         1.0  
1    -4.13416        M      23.8         2.5  
2    22.98422        M      16.0         3.5  
3   -60.06337        M      25.1         3.5  
4   -16.13497        M       5.0         4.0  
..        ...      ...       ...         ...  
366  34.85668        M      19.0         1.5  
367  28.60228        M      20.9         3.0  
368  31.75411        M      14.3         2.7  
369  25.46590        M      23.2         5.5  
370 -75.46073        M       8.6         3.0  

[371 rows x 8 columns]

In [9]:
def read_guvv(filename = '../ref/datafile2.txt',
                   data=pd.DataFrame(),csvfile=None):
    with open(filename) as f:
        table = f.readlines()[40:]
    for i,line in enumerate(table):
        if line.strip()=='':
            continue
        p = line[0:18].strip()
        pstring = f"{p[1:3]} {p[3:5]} {p[5:9]} {p[9:12]} {p[12:14]} {p[14:16]}"
        c = SkyCoord(pstring,unit=(u.hourangle,u.deg))
        entry = {
            'catalog':'GUVV',
            'catfile':filename,
            'GALEX ID':line[0:18].strip(), # source position as Jhhmmss.s+/-ddmmss.s (the table definition wrongly states Jhhmmss.ss+/-ddmmss.s)
            'SDSS ID':line[20:38].strip(),
            #'SIMBAD ID':line[40:68].strip()
            'ra':c.ra.deg,
            'dec':c.dec.deg,
            'nmag':float(line[89:94]), # maximum
            #'fmag':float(line[103:110]),
            #'spectype':'M',
            #'specsubtype':float(line[30:33]),
            #'distance':float(line[214:218]),
            }
        data = data.append(pd.Series(entry),ignore_index=True)
    return data

read_guvv()

catalog               catfile            GALEX ID            SDSS ID  \
0     GUVV  ../ref/datafile2.txt  J004347.9+421654.9  1322-0015866 CC A   
1     GUVV  ../ref/datafile2.txt  J004548.2-435509.1       0460-0006826   
2     GUVV  ../ref/datafile2.txt  J010732.6+360956.5  1261-0017670 1RXS   
3     GUVV  ../ref/datafile2.txt  J085218.1+311047.2       1211-0164505   
4     GUVV  ../ref/datafile2.txt  J090054.7+303113.3                      
..     ...                   ...                 ...                ...   
83    GUVV  ../ref/datafile2.txt  J123738.0-040841.2       0858-0232491   
84    GUVV  ../ref/datafile2.txt  J123913.5-113307.4  0784-0251397 NSVS   
85    GUVV  ../ref/datafile2.txt  J124109.1+230159.8       1130-0231256   
86    GUVV  ../ref/datafile2.txt  J124328.2-055431.7                      
87    GUVV  ../ref/datafile2.txt  J124746.2+243940.6       1146-0199030   

            ra        dec   nmag  
0    10.949583  42.281667  13.02  
1    11.450833 -43.919167  16.00  
2    16.885833  36.165556  20.01  
3   133.075417  31.179722  15.00  
4   135.227917  30.520278  19.69  
..         ...        ...    ...  
83  189.408333  -4.144722  18.50  
84  189.806250 -11.551944  17.09  
85  190.287917  23.033056  18.81  
86  190.867500  -5.908611  19.94  
87  191.942500  24.661111  18.58  

[88 rows x 7 columns]

In [10]:
def read_guvv2(filename = '../ref/aj274302_mrt2.txt',
                   data=pd.DataFrame(),csvfile=None):
    with open(filename) as f:
        table = f.readlines()[35:]
    for i,line in enumerate(table):
        if line.strip()=='':
            continue
        p = line[0:18].strip()
        pstring = f"{p[1:3]} {p[3:5]} {p[5:9]} {p[9:12]} {p[12:14]} {p[14:16]}"
        c = SkyCoord(pstring,unit=(u.hourangle,u.deg))
        entry = {
            'catalog':'GUVV2',
            'catfile':filename,
            'GALEX ID':line[0:18].strip(), # source position as Jhhmmss.s+/-ddmmss.s (the table definition wrongly states Jhhmmss.ss+/-ddmmss.s)
            'SDSS ID':line[20:38].strip(),
            #'SIMBAD ID':line[40:68].strip()
            'ra':c.ra.deg,
            'dec':c.dec.deg,
            'nmag':float(line[103:108]), # maximum
            #'fmag':float(line[103:110]),
            #'spectype':'M',
            #'specsubtype':float(line[30:33]),
            #'distance':float(line[214:218]),
            }
        data = data.append(pd.Series(entry),ignore_index=True)
    return data

read_guvv2()

catalog                   catfile            GALEX ID             SDSS ID  \
0     GUVV2  ../ref/aj274302_mrt2.txt  J001437.6-392632.2         505-0002317   
1     GUVV2  ../ref/aj274302_mrt2.txt  J001530.6-384855.9         511-0002596   
2     GUVV2  ../ref/aj274302_mrt2.txt  J001611.6-392721.5         505-0002614   
3     GUVV2  ../ref/aj274302_mrt2.txt  J002147.4+000031.3  002147.52+000030.9   
4     GUVV2  ../ref/aj274302_mrt2.txt  J002442.4+165808.0         069-0004486   
..      ...                       ...                 ...                 ...   
405   GUVV2  ../ref/aj274302_mrt2.txt  J224143.6+115326.2         018-0688549   
406   GUVV2  ../ref/aj274302_mrt2.txt  J225334.9-394830.4         501-0831641   
407   GUVV2  ../ref/aj274302_mrt2.txt  J225439.0-395240.8         501-0831843   
408   GUVV2  ../ref/aj274302_mrt2.txt  J234959.3-434817.8         461-0761490   
409   GUVV2  ../ref/aj274302_mrt2.txt  J235249.2-104826.7  235249.14-104828.4   

             ra        dec   nmag  
0      3.656667 -39.442222  19.38  
1      3.877500 -38.815278  19.02  
2      4.048333 -39.455833  16.16  
3      5.447500   0.008611  20.18  
4      6.176667  16.968889  17.68  
..          ...        ...    ...  
405  340.431667  11.890556  17.08  
406  343.395417 -39.808333  20.01  
407  343.662500 -39.877778  19.83  
408  357.497083 -43.804722  17.09  
409  358.205000 -10.807222  20.15  

[410 rows x 7 columns]

In [11]:
def read_gtds(filename = '../ref/apj462590t4_mrt.txt',
                   data=pd.DataFrame(),csvfile=None):
    with open(filename) as f:
        table = f.readlines()[60:]
    for i,line in enumerate(table):
        if line.strip()=='':
            continue
        entry = {
            'catalog':'GTDS',
            'catfile':filename,
            'GTDS ID':line[1:16].strip(),
            #'SIMBAD ID':line[40:68].strip()
            'ra':float(line[17:25]),
            'dec':float(line[27:34]),
            'nmag':float(line[37:42]), # minimum
            #'fmag':float(line[103:110]),
            #'spectype':'M',
            #'specsubtype':float(line[30:33]),
            #'distance':float(line[214:218]),
            'classification':line[92:104].strip(),
            }
        data = data.append(pd.Series(entry),ignore_index=True)
    return data

read_gtds()

catalog                     catfile          GTDS ID        ra      dec  \
0       GTDS  ../ref/apj462590t4_mrt.txt    ROTH_MOS01-21  216.1622  54.0911   
1       GTDS  ../ref/apj462590t4_mrt.txt  VDS22H_MOS05-05  333.8326  -0.5491   
2       GTDS  ../ref/apj462590t4_mrt.txt  LAISN1_MOS15-02  242.0397  54.3586   
3       GTDS  ../ref/apj462590t4_mrt.txt  LAISN1_MOS15-09  242.3685  53.6738   
4       GTDS  ../ref/apj462590t4_mrt.txt    ROTH_MOS07-09  212.5024  52.4153   
...      ...                         ...              ...       ...      ...   
1073    GTDS  ../ref/apj462590t4_mrt.txt  VDS22H_MOS05-00  333.4082  -0.7183   
1074    GTDS  ../ref/apj462590t4_mrt.txt   OSMOS_MOS23-20  150.9247   2.0944   
1075    GTDS  ../ref/apj462590t4_mrt.txt    ROTH_MOS04-15  212.2576  53.1997   
1076    GTDS  ../ref/apj462590t4_mrt.txt    ROTH_MOS06-03  214.1765  52.3035   
1077    GTDS  ../ref/apj462590t4_mrt.txt     DFS_MOS05-34   52.5501  26.9459   

       nmag classification  
0     22.54            Mdw  
1     21.14             CV  
2     22.89             CV  
3     23.03   Galaxy Trans  
4     23.10            Mdw  
...     ...            ...  
1073  18.06            QSO  
1074  19.20            AGN  
1075  19.79            RRL  
1076  18.54            QSO  
1077  18.23            AGN  

[1078 rows x 7 columns]

In [12]:
def ingest():
    # Compile a list of known M Dwarfs
    return pd.DataFrame().append(
        read_miles2017(),ignore_index=True,sort=False).append(
        read_dr7(),ignore_index=True,sort=False).append(
        read_pmsu(),ignore_index=True,sort=False).append(
        read_shkolnik2014(),ignore_index=True,sort=False).append(
        read_lepinegaidos(),ignore_index=True,sort=False).append(
        read_shkolnik2010(),ignore_index=True,sort=False).append(
        read_guvv(),ignore_index=True,sort=False).append(
        read_guvv2(),ignore_index=True,sort=False).append(
        read_gtds(),ignore_index=True,sort=False)

In [13]:
%time table = ingest()
len(table)

CPU times: user 14.8 s, sys: 20.7 ms, total: 14.8 s
Wall time: 14.8 s


11638

In [14]:
def angularSeparation(ra1, dec1, ra2, dec2):
    d2r = np.pi/180.
    ra2deg = 1./d2r
    d1 = dec1*d2r
    d2 = dec2*d2r
    r1 = ra1*d2r
    r2 = ra2*d2r
    a = np.sin((d2-d1)/2.)**2.+np.cos(d1)*np.cos(d2)*np.sin((r2-r1)/2.)**2.
    r = 2*np.arcsin(np.sqrt(a))
    return r*ra2deg

In [15]:
# Now do a crossmatch on the table to eliminate dupes
table_ = pd.DataFrame()
for i in np.arange(len(table)):
    if i==0:
        table_ = table_.append(table.iloc[i])
        continue
    ra,dec = table.iloc[i][['ra','dec']].values
    ras = table_['ra'].values
    decs = table_['dec'].values
    d = angularSeparation(ra,dec,ras,decs)
    if any(d<10/60/60): # 10 arcsecond crossmatch
        continue # source is already present
    table_ = table_.append(table.iloc[i])
print(len(table),len(table_))
table_

11638 10741


catalog                     catfile            source  \
0      MilesShkolnik2017       ../ref/1705.03583.txt           LHS1014   
1      MilesShkolnik2017       ../ref/1705.03583.txt           NLTT400   
2      MilesShkolnik2017       ../ref/1705.03583.txt           NLTT557   
3      MilesShkolnik2017       ../ref/1705.03583.txt  00144767-6003477   
4      MilesShkolnik2017       ../ref/1705.03583.txt            GJ1005   
...                  ...                         ...               ...   
11633               GTDS  ../ref/apj462590t4_mrt.txt               NaN   
11634               GTDS  ../ref/apj462590t4_mrt.txt               NaN   
11635               GTDS  ../ref/apj462590t4_mrt.txt               NaN   
11636               GTDS  ../ref/apj462590t4_mrt.txt               NaN   
11637               GTDS  ../ref/apj462590t4_mrt.txt               NaN   

              ra       dec spectype  distance specsubtype  ggoid   nmag  fmag  \
0        1.29780  45.78628        M      11.5         1.0    NaN    NaN   NaN   
1        2.30600  -4.13416        M      23.8         2.5    NaN    NaN   NaN   
2        2.97127  22.98422        M      16.0         3.5    NaN    NaN   NaN   
3        3.69901 -60.06337        M      25.1         3.5    NaN    NaN   NaN   
4        3.86861 -16.13497        M       5.0         4.0    NaN    NaN   NaN   
...          ...       ...      ...       ...         ...    ...    ...   ...   
11633  333.40820  -0.71830      NaN       NaN         NaN    NaN  18.06   NaN   
11634  150.92470   2.09440      NaN       NaN         NaN    NaN  19.20   NaN   
11635  212.25760  53.19970      NaN       NaN         NaN    NaN  19.79   NaN   
11636  214.17650  52.30350      NaN       NaN         NaN    NaN  18.54   NaN   
11637   52.55010  26.94590      NaN       NaN         NaN    NaN  18.23   NaN   

      GALEX ID SDSS ID          GTDS ID classification  
0          NaN     NaN              NaN            NaN  
1          NaN     NaN              NaN            NaN  
2          NaN     NaN              NaN            NaN  
3          NaN     NaN              NaN            NaN  
4          NaN     NaN              NaN            NaN  
...        ...     ...              ...            ...  
11633      NaN     NaN  VDS22H_MOS05-00            QSO  
11634      NaN     NaN   OSMOS_MOS23-20            AGN  
11635      NaN     NaN    ROTH_MOS04-15            RRL  
11636      NaN     NaN    ROTH_MOS06-03            QSO  
11637      NaN     NaN     DFS_MOS05-34            AGN  

[10741 rows x 15 columns]

In [16]:
header_data = pd.read_csv('../ref/mislike_image_header_table.csv')
catalog_filename = '../ref/catalog_nd_daostarfinder_decsort.parquet'
#catalog_file = pq.ParquetFile(catalog_filename)

In [42]:
def get_source(row,catalog_filename,obj_ids=[]):
    ra,dec = row[1][['ra','dec']].values
    this_area = pq.read_table(catalog_filename,filters =
                            [#('eclipse','=',eclipse),
                             #('obj_id','=',obj_id),
                             ('ra','>=',float(ra)-10/60/60), # 20" search box
                             ('ra','<=',float(ra)+10/60/60),
                             ('dec','>=',float(dec)-10/60/60),
                             ('dec','<=',float(dec)+10/60/60),
                             ('aperture_sum_edge_n_12_8','=',0.0),
                             ('aperture_sum_mask_n_12_8','=',0.0),
                            ],
                              columns = ['eclipse', 'ra', 'dec', 'obj_id', 'aperture_sum_n_12_8']
                         ).to_pandas()
    if not len(this_area):
        #print(f"# No MIS sources near {row[1]['catalog']}: {ra}, {dec}")
        return obj_ids
    for eclipse in this_area['eclipse'].unique():
        expt = header_data.loc[header_data['ECLIPSE']==eclipse].loc[header_data['BAND']=='NUV']['EXPT_0']
        minimum_integrated_counts = 0.5 * expt.values[0] # limiting magnitude of ~20.8 in NUV
        this_eclipse = this_area.loc[
            (this_area['eclipse']==eclipse) &
            (this_area['aperture_sum_n_12_8']>=minimum_integrated_counts)]
        try:
            ix = np.argmin(angularSeparation(ra,dec,
                    this_eclipse['ra'].values,
                    this_eclipse['dec'].values))
        except ValueError:
            #print(f'No matching source for e{eclipse}')
            continue
        obj_id = int(this_eclipse.iloc[ix]['obj_id'])
        if obj_id in obj_ids:
            print(f'#{obj_id} : skipping repeat')
            continue
        else:
            obj_ids+=[obj_id]
        print('python make_gfcat.py',
              int(eclipse),int(obj_id),
              f"# {row[1]['catalog']}: {ra}, {dec}")
    return obj_ids

    gc.collect()

def generate_target_list(table):
    obj_ids=[]
    for row in table.iterrows():
        obj_ids = get_source(row,catalog_filename,obj_ids=obj_ids)
        gc.collect()
    print(len(obj_ids))
    
generate_target_list(table)

python make_gfcat.py 17906 1807317906 # MilesShkolnik2017: 2.306, -4.13416
python make_gfcat.py 7809 2927707809 # MilesShkolnik2017: 2.306, -4.13416
python make_gfcat.py 7808 1514507808 # MilesShkolnik2017: 2.306, -4.13416
python make_gfcat.py 12664 2173512664 # MilesShkolnik2017: 2.306, -4.13416
python make_gfcat.py 2115 1862902115 # MilesShkolnik2017: 8.90835, -10.07196
python make_gfcat.py 34382 1361034382 # MilesShkolnik2017: 19.16491, 25.33127
python make_gfcat.py 8234 994008234 # MilesShkolnik2017: 19.16491, 25.33127
python make_gfcat.py 8348 1061908348 # MilesShkolnik2017: 19.16491, 25.33127
python make_gfcat.py 8347 1031808347 # MilesShkolnik2017: 19.16491, 25.33127
python make_gfcat.py 40362 125240362 # MilesShkolnik2017: 19.46035, 28.67011
python make_gfcat.py 13648 622413648 # MilesShkolnik2017: 24.76279, -17.94948
python make_gfcat.py 13649 593813649 # MilesShkolnik2017: 24.76279, -17.94948
python make_gfcat.py 13655 597813655 # MilesShkolnik2017: 24.76279, -17.94948
python

python make_gfcat.py 3768 739403768 # MilesShkolnik2017: 121.72992, 42.29207
python make_gfcat.py 30695 1106130695 # MilesShkolnik2017: 133.18605, 22.51426
python make_gfcat.py 25834 618525834 # MilesShkolnik2017: 134.08146, 12.66344
python make_gfcat.py 25831 618225831 # MilesShkolnik2017: 134.08146, 12.66344
python make_gfcat.py 25832 1559025832 # MilesShkolnik2017: 134.08146, 12.66344
python make_gfcat.py 25833 1619725833 # MilesShkolnik2017: 134.08146, 12.66344
python make_gfcat.py 26121 700526121 # MilesShkolnik2017: 134.66045, 20.54641
python make_gfcat.py 30792 840730792 # MilesShkolnik2017: 135.09723, 21.83369
python make_gfcat.py 30391 742030391 # MilesShkolnik2017: 135.09723, 21.83369
python make_gfcat.py 35843 1895635843 # MilesShkolnik2017: 135.13424, 46.58557
python make_gfcat.py 14646 2711414646 # MilesShkolnik2017: 138.90101, -10.59677
python make_gfcat.py 10046 1628310046 # MilesShkolnik2017: 138.90101, -10.59677
python make_gfcat.py 10044 1673110044 # MilesShkolnik2017

python make_gfcat.py 11875 1135011875 # MilesShkolnik2017: 247.82792, 40.86492
python make_gfcat.py 10861 595810861 # MilesShkolnik2017: 247.82792, 40.86492
python make_gfcat.py 10821 606910821 # MilesShkolnik2017: 247.82792, 40.86492
python make_gfcat.py 17294 1104717294 # MilesShkolnik2017: 247.82792, 40.86492
python make_gfcat.py 10905 601510905 # MilesShkolnik2017: 247.82792, 40.86492
python make_gfcat.py 11876 1249611876 # MilesShkolnik2017: 247.82792, 40.86492
python make_gfcat.py 10909 600610909 # MilesShkolnik2017: 247.82792, 40.86492
python make_gfcat.py 17115 719317115 # MilesShkolnik2017: 247.82792, 40.86492
python make_gfcat.py 17295 1214717295 # MilesShkolnik2017: 247.82792, 40.86492
python make_gfcat.py 17096 615817096 # MilesShkolnik2017: 247.82792, 40.86492
python make_gfcat.py 10802 655810802 # MilesShkolnik2017: 247.82792, 40.86492
python make_gfcat.py 17292 961517292 # MilesShkolnik2017: 247.82792, 40.86492
python make_gfcat.py 17070 659917070 # MilesShkolnik2017: 24

python make_gfcat.py 39498 1887939498 # MilesShkolnik2017: 331.46322, -11.91451
python make_gfcat.py 17863 1601017863 # MilesShkolnik2017: 333.42998, -17.6862
python make_gfcat.py 17416 485417416 # MilesShkolnik2017: 333.42998, -17.6862
python make_gfcat.py 22972 495722972 # MilesShkolnik2017: 333.42998, -17.6862
python make_gfcat.py 13019 580013019 # MilesShkolnik2017: 333.42998, -17.6862
python make_gfcat.py 2045 345802045 # MilesShkolnik2017: 333.42998, -17.6862
python make_gfcat.py 22929 663922929 # MilesShkolnik2017: 333.42998, -17.6862
python make_gfcat.py 12954 305412954 # MilesShkolnik2017: 333.42998, -17.6862
python make_gfcat.py 13017 1853513017 # MilesShkolnik2017: 333.42998, -17.6862
python make_gfcat.py 22944 721622944 # MilesShkolnik2017: 333.42998, -17.6862
python make_gfcat.py 28376 335528376 # MilesShkolnik2017: 333.42998, -17.6862
python make_gfcat.py 18244 704618244 # MilesShkolnik2017: 333.42998, -17.6862
python make_gfcat.py 22892 552322892 # MilesShkolnik2017: 333

python make_gfcat.py 42052 738442052 # DR7: 182.30648, 43.476725
python make_gfcat.py 8108 1572608108 # DR7: 13.7684831, -0.6646526
python make_gfcat.py 8079 2009308079 # DR7: 13.7684831, -0.6646526
python make_gfcat.py 29018 524429018 # DR7: 13.7684831, -0.6646526
python make_gfcat.py 29349 339629349 # DR7: 13.7684831, -0.6646526
python make_gfcat.py 8108 1130008108 # DR7: 13.6438482, -0.9820911
python make_gfcat.py 8114 572808114 # DR7: 13.6438482, -0.9820911
python make_gfcat.py 23613 331923613 # DR7: 13.6438482, -0.9820911
python make_gfcat.py 29018 315729018 # DR7: 13.6438482, -0.9820911
python make_gfcat.py 29349 198929349 # DR7: 13.6438482, -0.9820911
python make_gfcat.py 8079 1500108079 # DR7: 13.6438482, -0.9820911
python make_gfcat.py 11220 1343811220 # DR7: 214.934972, 52.3236012
python make_gfcat.py 835 1774000835 # DR7: 214.934972, 52.3236012
python make_gfcat.py 10640 844010640 # DR7: 214.934972, 52.3236012
python make_gfcat.py 807 1533400807 # DR7: 214.934972, 52.3236012

...

python make_gfcat.py 32244 1217332244 # GTDS: 213.0591, 53.4297
python make_gfcat.py 32810 1268632810 # GTDS: 213.0591, 53.4297
python make_gfcat.py 36758 1668036758 # GTDS: 213.0591, 53.4297
python make_gfcat.py 37398 1431137398 # GTDS: 213.0591, 53.4297
python make_gfcat.py 42016 940342016 # GTDS: 213.0591, 53.4297
python make_gfcat.py 36699 1049936699 # GTDS: 213.0591, 53.4297
python make_gfcat.py 41987 970541987 # GTDS: 213.0591, 53.4297
python make_gfcat.py 37339 1315037339 # GTDS: 213.0591, 53.4297
python make_gfcat.py 37309 1264037309 # GTDS: 213.0591, 53.4297
python make_gfcat.py 32215 1259032215 # GTDS: 213.0591, 53.4297
python make_gfcat.py 36727 977736727 # GTDS: 213.0591, 53.4297
python make_gfcat.py 32781 1092232781 # GTDS: 213.0591, 53.4297
python make_gfcat.py 37367 1375337367 # GTDS: 213.0591, 53.4297
python make_gfcat.py 36817 920636817 # GTDS: 213.0591, 53.4297
python make_gfcat.py 32835 1488332835 # GTDS: 213.0591, 53.4297
python make_gfcat.py 32179 1409832179 # GTDS

python make_gfcat.py 28338 1399028338 # GTDS: 333.8612, 1.2322
python make_gfcat.py 39221 1647139221 # GTDS: 333.8612, 1.2322
python make_gfcat.py 33627 1489033627 # GTDS: 333.8612, 1.2322
python make_gfcat.py 38860 1794538860 # GTDS: 333.8612, 1.2322
python make_gfcat.py 34182 1053234182 # GTDS: 333.8612, 1.2322
python make_gfcat.py 33772 1966433772 # GTDS: 333.8612, 1.2322
python make_gfcat.py 38719 2403338719 # GTDS: 333.8612, 1.2322
python make_gfcat.py 33597 1467733597 # GTDS: 333.8612, 1.2322
python make_gfcat.py 33681 1538333681 # GTDS: 333.8612, 1.2322
python make_gfcat.py 34042 1513934042 # GTDS: 333.8612, 1.2322
python make_gfcat.py 33656 1509533656 # GTDS: 333.8612, 1.2322
python make_gfcat.py 28621 1143028621 # GTDS: 333.8612, 1.2322
python make_gfcat.py 44214 2688844214 # GTDS: 333.8612, 1.2322
python make_gfcat.py 33978 1295633978 # GTDS: 333.8612, 1.2322
python make_gfcat.py 38826 1746838826 # GTDS: 333.8612, 1.2322
python make_gfcat.py 33922 1332933922 # GTDS: 333.8612,

python make_gfcat.py 4781 1345704781 # GTDS: 150.8654, 1.9623
python make_gfcat.py 14685 3590114685 # GTDS: 150.8654, 1.9623
python make_gfcat.py 41603 599341603 # GTDS: 150.8654, 1.9623
python make_gfcat.py 15405 1530215405 # GTDS: 150.8654, 1.9623
python make_gfcat.py 4218 2116004218 # GTDS: 150.8654, 1.9623
python make_gfcat.py 4291 2374104291 # GTDS: 150.8654, 1.9623
python make_gfcat.py 41519 681841519 # GTDS: 150.8654, 1.9623
python make_gfcat.py 36188 784236188 # GTDS: 150.8654, 1.9623
python make_gfcat.py 26166 502626166 # GTDS: 150.8654, 1.9623
python make_gfcat.py 19989 1658119989 # GTDS: 150.8654, 1.9623
python make_gfcat.py 15431 1546615431 # GTDS: 150.8654, 1.9623
python make_gfcat.py 36389 574636389 # GTDS: 150.8654, 1.9623
python make_gfcat.py 25915 1234525915 # GTDS: 150.8654, 1.9623
python make_gfcat.py 25980 556725980 # GTDS: 150.8654, 1.9623
python make_gfcat.py 4454 1355104454 # GTDS: 150.8654, 1.9623
python make_gfcat.py 25355 1070025355 # GTDS: 150.8654, 1.9623
py

python make_gfcat.py 10704 384410704 # GTDS: 214.6603, 52.4
python make_gfcat.py 11205 1036011205 # GTDS: 214.6603, 52.4
python make_gfcat.py 10589 477410589 # GTDS: 214.6603, 52.4
python make_gfcat.py 15758 479415758 # GTDS: 214.6603, 52.4
python make_gfcat.py 10669 484210669 # GTDS: 214.6603, 52.4
python make_gfcat.py 15764 502615764 # GTDS: 214.6603, 52.4
python make_gfcat.py 15179 526715179 # GTDS: 214.6603, 52.4
python make_gfcat.py 9985 409609985 # GTDS: 214.6603, 52.4
python make_gfcat.py 21067 407021067 # GTDS: 214.6603, 52.4
python make_gfcat.py 15182 407315182 # GTDS: 214.6603, 52.4
python make_gfcat.py 10012 604210012 # GTDS: 214.6603, 52.4
python make_gfcat.py 15234 356715234 # GTDS: 214.6603, 52.4
python make_gfcat.py 11216 495711216 # GTDS: 214.6603, 52.4
python make_gfcat.py 10026 825010026 # GTDS: 214.6603, 52.4
python make_gfcat.py 9932 391809932 # GTDS: 214.6603, 52.4
python make_gfcat.py 10016 370410016 # GTDS: 214.6603, 52.4
python make_gfcat.py 15226 395515226 # GT

python make_gfcat.py 4222 2115904222 # GTDS: 150.9247, 2.0944
python make_gfcat.py 25355 1172425355 # GTDS: 150.9247, 2.0944
python make_gfcat.py 36505 738136505 # GTDS: 150.9247, 2.0944
python make_gfcat.py 4305 2911304305 # GTDS: 150.9247, 2.0944
python make_gfcat.py 41630 681341630 # GTDS: 150.9247, 2.0944
python make_gfcat.py 4247 2118304247 # GTDS: 150.9247, 2.0944
python make_gfcat.py 36245 956936245 # GTDS: 150.9247, 2.0944
python make_gfcat.py 41519 800941519 # GTDS: 150.9247, 2.0944
python make_gfcat.py 25599 587725599 # GTDS: 150.9247, 2.0944
python make_gfcat.py 4623 1517904623 # GTDS: 150.9247, 2.0944
python make_gfcat.py 36563 644836563 # GTDS: 150.9247, 2.0944
python make_gfcat.py 25331 1334725331 # GTDS: 150.9247, 2.0944
python make_gfcat.py 36128 667336128 # GTDS: 150.9247, 2.0944
python make_gfcat.py 42113 1282442113 # GTDS: 150.9247, 2.0944
python make_gfcat.py 26128 962426128 # GTDS: 150.9247, 2.0944
python make_gfcat.py 36271 977436271 # GTDS: 150.9247, 2.0944
pytho

In [43]:
58381*3/60/60

48.65083333333334